# Amazon Sales Report Analysis
## Comprehensive Business Intelligence & Actionable Insights

**Objective:** Analyze Amazon sales data to extract insights on sales performance, product preferences, fulfillment effectiveness, customer behavior, and geographical distribution to drive business growth.

## Section 1: Load and Explore the Dataset

Load required libraries and import the Amazon sales dataset to understand its structure and content.

In [1]:
# Import Required Libraries
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import warnings
warnings.filterwarnings('ignore')

# Set style for visualizations
sns.set_style("whitegrid")
plt.rcParams['figure.figsize'] = (14, 6)

# Load the dataset
file_path = r'c:\Users\binit\Desktop\work\infosdata analyst\Amazon Sale Report.csv'
df = pd.read_csv(file_path, encoding='latin-1')

print("="*80)
print("DATASET OVERVIEW")
print("="*80)
print(f"\nDataset Shape: {df.shape}")
print(f"\nColumn Names and Data Types:\n{df.dtypes}")
print(f"\nFirst Few Rows:\n{df.head()}")
print(f"\nDataset Info:\n")
df.info()
print(f"\nBasic Statistics:\n{df.describe()}")

DATASET OVERVIEW

Dataset Shape: (128976, 21)

Column Names and Data Types:
index                   int64
Order ID               object
Date                   object
Status                 object
Fulfilment             object
Sales Channel          object
ship-service-level     object
Category               object
Size                   object
Courier Status         object
Qty                     int64
currency               object
Amount                float64
ship-city              object
ship-state             object
ship-postal-code      float64
ship-country           object
B2B                      bool
fulfilled-by           object
New                   float64
PendingS              float64
dtype: object

First Few Rows:
   index             Order ID      Date                        Status  \
0      0  405-8078784-5731545  04-30-22                     Cancelled   
1      1  171-9198151-1101146  04-30-22  Shipped - Delivered to Buyer   
2      2  404-0687676-7273146  04-30-22     

## Section 2: Data Cleaning and Preprocessing

Handle missing values, standardize formats, and prepare data for analysis.

In [2]:
# Check for missing values
print("="*80)
print("MISSING VALUES ANALYSIS")
print("="*80)
missing_data = pd.DataFrame({
    'Column': df.columns,
    'Missing_Count': df.isnull().sum(),
    'Missing_Percentage': (df.isnull().sum() / len(df)) * 100
})
print(missing_data[missing_data['Missing_Count'] > 0])

# Data Cleaning
df_clean = df.copy()

# Convert Date column to datetime (handle mixed formats)
df_clean['Date'] = pd.to_datetime(df_clean['Date'], format='mixed', dayfirst=False)

# Fill missing Amount with 0 for cancelled orders
df_clean['Amount'] = pd.to_numeric(df_clean['Amount'], errors='coerce').fillna(0)

# Remove extra spaces from string columns
string_columns = df_clean.select_dtypes(include=['object']).columns
for col in string_columns:
    df_clean[col] = df_clean[col].str.strip()

# Standardize city names (remove inconsistencies)
df_clean['ship-city'] = df_clean['ship-city'].str.upper()

# Convert Qty to numeric
df_clean['Qty'] = pd.to_numeric(df_clean['Qty'], errors='coerce').fillna(0)

# Remove duplicates
initial_rows = len(df_clean)
df_clean = df_clean.drop_duplicates()
print(f"\nDuplicates Removed: {initial_rows - len(df_clean)}")

# Create additional useful columns
df_clean['Year'] = df_clean['Date'].dt.year
df_clean['Month'] = df_clean['Date'].dt.month
df_clean['Month_Name'] = df_clean['Date'].dt.strftime('%B')
df_clean['Week'] = df_clean['Date'].dt.isocalendar().week
df_clean['Day_of_Week'] = df_clean['Date'].dt.day_name()

print(f"\n✓ Data Cleaning Complete!")
print(f"Final Dataset Shape: {df_clean.shape}")
print(f"\nDate Range: {df_clean['Date'].min()} to {df_clean['Date'].max()}")

MISSING VALUES ANALYSIS
                            Column  Missing_Count  Missing_Percentage
currency                  currency           7800            6.047637
Amount                      Amount           7800            6.047637
ship-city                ship-city             35            0.027137
ship-state              ship-state             35            0.027137
ship-postal-code  ship-postal-code             35            0.027137
ship-country          ship-country             35            0.027137
fulfilled-by          fulfilled-by          89713           69.557902
New                            New         128976          100.000000
PendingS                  PendingS         128976          100.000000

Duplicates Removed: 168

✓ Data Cleaning Complete!
Final Dataset Shape: (128808, 26)

Date Range: 2022-03-31 00:00:00 to 2022-06-29 00:00:00


## Section 3: Sales Overview and Trends Analysis

Analyze sales performance, identify trends, and uncover seasonal patterns.

In [3]:
# Sales Overview Metrics
print("="*80)
print("SALES OVERVIEW METRICS")
print("="*80)

total_orders = len(df_clean)
completed_orders = len(df_clean[df_clean['Status'].isin(['Shipped', 'Shipped - Delivered to Buyer'])])
cancelled_orders = len(df_clean[df_clean['Status'] == 'Cancelled'])
total_revenue = df_clean['Amount'].sum()
avg_order_value = df_clean[df_clean['Amount'] > 0]['Amount'].mean()
total_quantity = df_clean['Qty'].sum()

print(f"\nTotal Orders: {total_orders:,}")
print(f"Completed Orders: {completed_orders:,} ({(completed_orders/total_orders)*100:.2f}%)")
print(f"Cancelled Orders: {cancelled_orders:,} ({(cancelled_orders/total_orders)*100:.2f}%)")
print(f"Total Revenue: ₹{total_revenue:,.2f}")
print(f"Average Order Value: ₹{avg_order_value:,.2f}")
print(f"Total Quantity Sold: {total_quantity:,.0f}")

# Status Distribution
status_dist = df_clean['Status'].value_counts()
print(f"\nOrder Status Distribution:\n{status_dist}")

# Daily Sales Trend
daily_sales = df_clean.groupby('Date').agg({
    'Order ID': 'count',
    'Amount': 'sum',
    'Qty': 'sum'
}).reset_index()
daily_sales.columns = ['Date', 'Orders', 'Revenue', 'Quantity']

# Visualization: Daily Sales Trend
fig = make_subplots(
    rows=3, cols=1,
    subplot_titles=('Daily Orders', 'Daily Revenue (₹)', 'Daily Quantity Sold'),
    specs=[[{"secondary_y": False}], [{"secondary_y": False}], [{"secondary_y": False}]]
)

fig.add_trace(go.Scatter(x=daily_sales['Date'], y=daily_sales['Orders'], 
                        mode='lines', name='Orders', line=dict(color='#1f77b4')), row=1, col=1)
fig.add_trace(go.Scatter(x=daily_sales['Date'], y=daily_sales['Revenue'], 
                        mode='lines', name='Revenue', line=dict(color='#2ca02c')), row=2, col=1)
fig.add_trace(go.Scatter(x=daily_sales['Date'], y=daily_sales['Quantity'], 
                        mode='lines', name='Quantity', line=dict(color='#ff7f0e')), row=3, col=1)

fig.update_yaxes(title_text="Orders", row=1, col=1)
fig.update_yaxes(title_text="Revenue (₹)", row=2, col=1)
fig.update_yaxes(title_text="Quantity", row=3, col=1)
fig.update_xaxes(title_text="Date", row=3, col=1)
fig.update_layout(height=800, title_text="Sales Trends Over Time", showlegend=False)
fig.show()

# Monthly Sales Analysis
monthly_sales = df_clean.groupby('Month_Name').agg({
    'Order ID': 'count',
    'Amount': 'sum',
    'Qty': 'sum'
}).reset_index()
monthly_sales.columns = ['Month', 'Orders', 'Revenue', 'Quantity']

print(f"\nMonthly Sales Summary:\n{monthly_sales}")

SALES OVERVIEW METRICS

Total Orders: 128,808
Completed Orders: 106,428 (82.63%)
Cancelled Orders: 18,311 (14.22%)
Total Revenue: ₹78,496,786.39
Average Order Value: ₹661.42
Total Quantity Sold: 116,496

Order Status Distribution:
Status
Shipped                          77713
Shipped - Delivered to Buyer     28715
Cancelled                        18311
Shipped - Returned to Seller      1952
Shipped - Picked Up                973
Pending                            658
Pending - Waiting for Pick Up      281
Shipped - Returning to Seller      145
Shipped - Out for Delivery          35
Shipped - Rejected by Buyer         11
Shipping                             8
Shipped - Lost in Transit            5
Shipped - Damaged                    1
Name: count, dtype: int64



Monthly Sales Summary:
   Month  Orders      Revenue  Quantity
0  April   48900  28742816.41     44053
1   June   37697  23425809.38     34276
2  March     171    101683.85       156
3    May   42040  26226476.75     38011


In [4]:
# Visualization: Order Status Distribution
fig_status = px.pie(names=status_dist.index, values=status_dist.values, 
                    title='Order Status Distribution',
                    color_discrete_sequence=px.colors.qualitative.Set2)
fig_status.show()

# Day of Week Analysis
dow_sales = df_clean.groupby('Day_of_Week').agg({
    'Order ID': 'count',
    'Amount': 'sum'
}).reset_index()
dow_sales.columns = ['Day', 'Orders', 'Revenue']

# Define day order
day_order = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']
dow_sales['Day'] = pd.Categorical(dow_sales['Day'], categories=day_order, ordered=True)
dow_sales = dow_sales.sort_values('Day')

fig_dow = make_subplots(specs=[[{"secondary_y": True}]])
fig_dow.add_trace(go.Bar(x=dow_sales['Day'], y=dow_sales['Orders'], 
                         name='Orders', marker_color='lightblue'), secondary_y=False)
fig_dow.add_trace(go.Scatter(x=dow_sales['Day'], y=dow_sales['Revenue'], 
                             name='Revenue', mode='lines+markers', line=dict(color='red')), secondary_y=True)

fig_dow.update_layout(title='Sales by Day of Week', hovermode='x unified')
fig_dow.update_yaxes(title_text="Orders", secondary_y=False)
fig_dow.update_yaxes(title_text="Revenue (₹)", secondary_y=True)
fig_dow.show()

## Section 4: Product Analysis

Analyze product categories, sizes, and quantities to identify popular products and trends.

In [5]:
# Product Category Analysis
print("="*80)
print("PRODUCT ANALYSIS")
print("="*80)

category_stats = df_clean.groupby('Category').agg({
    'Order ID': 'count',
    'Amount': ['sum', 'mean'],
    'Qty': 'sum'
}).round(2)
category_stats.columns = ['Orders', 'Total_Revenue', 'Avg_Price', 'Total_Qty']
category_stats = category_stats.sort_values('Orders', ascending=False)
print(f"\nProduct Category Performance:\n{category_stats}")

# Top 10 Categories by Revenue
top_categories_revenue = category_stats.sort_values('Total_Revenue', ascending=False).head(10)

fig_cat = px.bar(top_categories_revenue.reset_index(), x='Category', y='Total_Revenue',
                 title='Top 10 Product Categories by Revenue', color='Total_Revenue',
                 color_continuous_scale='Viridis', labels={'Total_Revenue': 'Revenue (₹)'})
fig_cat.update_layout(xaxis_tickangle=-45)
fig_cat.show()

# Size Analysis
print("\nSize Distribution:")
size_dist = df_clean['Size'].value_counts()
print(size_dist)

# Top sizes by orders and revenue
size_stats = df_clean.groupby('Size').agg({
    'Order ID': 'count',
    'Amount': 'sum'
}).reset_index()
size_stats.columns = ['Size', 'Orders', 'Revenue']
size_stats = size_stats.sort_values('Orders', ascending=False)

fig_size = px.bar(size_stats, x='Size', y='Orders', 
                  color='Revenue', title='Product Sales by Size',
                  color_continuous_scale='Blues', labels={'Orders': 'Number of Orders'})
fig_size.show()

# Category-Size Cross Analysis
category_size = df_clean.groupby(['Category', 'Size']).size().reset_index(name='Orders')
category_size_top = category_size.nlargest(15, 'Orders')

fig_cs = px.bar(category_size_top, x='Category', y='Orders', color='Size',
                title='Top 15 Category-Size Combinations',
                barmode='group', labels={'Orders': 'Number of Orders'})
fig_cs.update_layout(xaxis_tickangle=-45)
fig_cs.show()

PRODUCT ANALYSIS

Product Category Performance:
          Orders  Total_Revenue  Avg_Price  Total_Qty
Category                                             
T-shirt    50219    39154132.17     779.67      45228
Shirt      49804    21269768.70     427.07      44978
Blazzer    15489    11208506.12     723.64      13934
Trousers   10607     5341305.30     503.56       9889
Perfume     1157      789419.66     682.30       1051
Wallet       926      458408.18     495.04        863
Socks        439      150397.50     342.59        398
Shoes        164      123933.76     755.69        152
Watch          3         915.00     305.00          3



Size Distribution:
Size
M       22350
L       21777
XL      20520
XXL     17783
S       16754
3XL     14626
XS      11033
Free     2250
6XL       738
5XL       550
4XL       427
Name: count, dtype: int64


## Section 5: Fulfillment Analysis

Analyze fulfillment methods and their effectiveness in delivering orders.

In [6]:
# Fulfillment Analysis
print("="*80)
print("FULFILLMENT ANALYSIS")
print("="*80)

fulfillment_stats = df_clean.groupby('Fulfilment').agg({
    'Order ID': 'count',
    'Amount': 'sum',
    'Qty': 'sum'
}).reset_index()
fulfillment_stats.columns = ['Fulfillment', 'Orders', 'Revenue', 'Quantity']
print(f"\nFulfillment Method Performance:\n{fulfillment_stats}")

# Fulfillment by Status
print("\nFulfillment vs Order Status:")
fulfillment_status = pd.crosstab(df_clean['Fulfilment'], df_clean['Status'], margins=True)
print(fulfillment_status)

# Calculate delivery success rate
successful_fulfillment = df_clean[df_clean['Status'] != 'Cancelled'].groupby('Fulfilment').size()
total_fulfillment = df_clean.groupby('Fulfilment').size()
success_rate = (successful_fulfillment / total_fulfillment * 100).round(2)
print(f"\nFulfillment Success Rate:\n{success_rate}")

# Visualization: Fulfillment Channel Performance
fig_fulf = make_subplots(specs=[[{"secondary_y": True}]])
fig_fulf.add_trace(go.Bar(x=fulfillment_stats['Fulfillment'], y=fulfillment_stats['Orders'],
                          name='Orders', marker_color='skyblue'), secondary_y=False)
fig_fulf.add_trace(go.Scatter(x=fulfillment_stats['Fulfillment'], y=fulfillment_stats['Revenue'],
                              name='Revenue', mode='lines+markers', marker=dict(size=10),
                              line=dict(color='red', width=3)), secondary_y=True)

fig_fulf.update_layout(title='Fulfillment Channel Performance', hovermode='x unified')
fig_fulf.update_yaxes(title_text="Orders", secondary_y=False)
fig_fulf.update_yaxes(title_text="Revenue (₹)", secondary_y=True)
fig_fulf.show()

# Shipping Service Level Analysis
print("\nShipping Service Level Distribution:")
service_level_stats = df_clean['ship-service-level'].value_counts()
print(service_level_stats)

service_level_revenue = df_clean.groupby('ship-service-level').agg({
    'Amount': 'sum',
    'Order ID': 'count'
}).reset_index()
service_level_revenue.columns = ['Service Level', 'Revenue', 'Orders']

fig_service = px.bar(service_level_revenue, x='Service Level', y=['Revenue', 'Orders'],
                     barmode='group', title='Revenue and Orders by Shipping Service Level')
fig_service.show()

# Courier Status Analysis
print("\nCourier Status Distribution:")
courier_status = df_clean['Courier Status'].value_counts()
print(courier_status)

FULFILLMENT ANALYSIS

Fulfillment Method Performance:
  Fulfillment  Orders      Revenue  Quantity
0      Amazon   89595  54262165.00     83990
1    Merchant   39213  24234621.39     32506

Fulfillment vs Order Status:
Status      Cancelled  Pending  Pending - Waiting for Pick Up  Shipped  \
Fulfilment                                                               
Amazon          11459      415                              0    77713   
Merchant         6852      243                            281        0   
All             18311      658                            281    77713   

Status      Shipped - Damaged  Shipped - Delivered to Buyer  \
Fulfilment                                                    
Amazon                      0                             0   
Merchant                    1                         28715   
All                         1                         28715   

Status      Shipped - Lost in Transit  Shipped - Out for Delivery  \
Fulfilment               


Shipping Service Level Distribution:
ship-service-level
Expedited    88513
Standard     40295
Name: count, dtype: int64



Courier Status Distribution:
Courier Status
Shipped       109341
On the Way      6863
Unshipped       6675
Cancelled       5929
Name: count, dtype: int64


## Section 6: Customer Segmentation

Segment customers based on purchase behavior, location, and spending patterns.

In [7]:
# Customer Segmentation Analysis
print("="*80)
print("CUSTOMER SEGMENTATION ANALYSIS")
print("="*80)

# Calculate customer metrics
customer_metrics = df_clean.groupby('Order ID').agg({
    'Amount': 'sum',
    'Qty': 'sum',
    'ship-state': 'first',
    'ship-city': 'first',
    'Date': 'first',
    'Status': 'first'
}).reset_index()

# Customer purchase frequency and value
customer_purchase = df_clean.groupby('Order ID').agg({
    'Amount': 'sum',
    'Qty': 'sum',
    'ship-city': 'first'
}).reset_index()
customer_purchase.columns = ['Order_ID', 'Total_Spent', 'Total_Qty', 'City']

# Segmentation based on spending
def segment_customer(amount):
    if amount == 0:
        return 'Cancelled'
    elif amount < 400:
        return 'Low Value'
    elif amount < 700:
        return 'Medium Value'
    else:
        return 'High Value'

customer_purchase['Segment'] = customer_purchase['Total_Spent'].apply(segment_customer)

segment_analysis = customer_purchase.groupby('Segment').agg({
    'Order_ID': 'count',
    'Total_Spent': ['sum', 'mean'],
    'Total_Qty': 'mean'
}).round(2)
segment_analysis.columns = ['Number_of_Orders', 'Total_Revenue', 'Avg_Order_Value', 'Avg_Qty']
print(f"\nCustomer Segmentation by Value:\n{segment_analysis}")

# Visualization: Customer Segment Distribution
fig_segment = px.pie(customer_purchase, names='Segment', values='Order_ID',
                    title='Customer Segmentation Distribution',
                    color_discrete_sequence=px.colors.qualitative.Set3)
fig_segment.show()

# Revenue by Customer Segment
fig_segment_revenue = px.bar(segment_analysis.reset_index(), x='Segment', y='Total_Revenue',
                             title='Total Revenue by Customer Segment', 
                             color='Segment', color_discrete_sequence=px.colors.qualitative.Set2,
                             labels={'Total_Revenue': 'Revenue (₹)'})
fig_segment_revenue.show()

# B2B vs B2C Analysis
print("\nB2B vs B2C Analysis:")
b2b_analysis = df_clean.groupby('B2B').agg({
    'Order ID': 'count',
    'Amount': 'sum',
    'Qty': 'sum'
}).reset_index()
b2b_analysis['B2B'] = b2b_analysis['B2B'].map({True: 'B2B', False: 'B2C'})
b2b_analysis.columns = ['Type', 'Orders', 'Revenue', 'Quantity']
print(b2b_analysis)

fig_b2b = make_subplots(specs=[[{"secondary_y": True}]])
fig_b2b.add_trace(go.Bar(x=b2b_analysis['Type'], y=b2b_analysis['Orders'],
                         name='Orders', marker_color='lightgreen'), secondary_y=False)
fig_b2b.add_trace(go.Scatter(x=b2b_analysis['Type'], y=b2b_analysis['Revenue'],
                             name='Revenue', mode='lines+markers', line=dict(color='darkgreen', width=3)),
                  secondary_y=True)

fig_b2b.update_layout(title='B2B vs B2C Performance', hovermode='x unified')
fig_b2b.update_yaxes(title_text="Orders", secondary_y=False)
fig_b2b.update_yaxes(title_text="Revenue (₹)", secondary_y=True)
fig_b2b.show()

CUSTOMER SEGMENTATION ANALYSIS

Customer Segmentation by Value:
              Number_of_Orders  Total_Revenue  Avg_Order_Value  Avg_Qty
Segment                                                                
Cancelled                 9682           0.00             0.00     0.26
High Value               46613    46803538.80          1004.09     1.13
Low Value                18316     6550656.63           357.65     0.95
Medium Value             45618    25142590.96           551.16     0.97



B2B vs B2C Analysis:
  Type  Orders      Revenue  Quantity
0  B2C  127937  77905565.60    115656
1  B2B     871    591220.79       840


## Section 7: Geographical Analysis

Explore sales distribution across states and cities to identify key markets.

In [8]:
# Geographical Analysis
print("="*80)
print("GEOGRAPHICAL ANALYSIS")
print("="*80)

# State-wise Analysis
state_analysis = df_clean.groupby('ship-state').agg({
    'Order ID': 'count',
    'Amount': 'sum',
    'Qty': 'sum'
}).reset_index()
state_analysis.columns = ['State', 'Orders', 'Revenue', 'Quantity']
state_analysis = state_analysis.sort_values('Revenue', ascending=False)

print(f"\nTop 15 States by Revenue:\n{state_analysis.head(15)}")

# Top 15 States Visualization
fig_state = px.bar(state_analysis.head(15), x='State', y='Revenue',
                   color='Orders', title='Top 15 States by Revenue',
                   color_continuous_scale='Plasma', labels={'Revenue': 'Revenue (₹)', 'Orders': 'Number of Orders'})
fig_state.update_layout(xaxis_tickangle=-45)
fig_state.show()

# City-wise Analysis
city_analysis = df_clean.groupby('ship-city').agg({
    'Order ID': 'count',
    'Amount': 'sum'
}).reset_index()
city_analysis.columns = ['City', 'Orders', 'Revenue']
city_analysis = city_analysis.sort_values('Revenue', ascending=False)

print(f"\nTop 15 Cities by Revenue:\n{city_analysis.head(15)}")

# Top 15 Cities Visualization
fig_city = px.bar(city_analysis.head(15), x='City', y='Revenue',
                  color='Orders', title='Top 15 Cities by Revenue',
                  color_continuous_scale='Viridis', labels={'Revenue': 'Revenue (₹)'})
fig_city.update_layout(xaxis_tickangle=-45)
fig_city.show()

# State wise order count
state_orders = state_analysis.sort_values('Orders', ascending=False).head(15)
fig_state_orders = px.bar(state_orders, x='State', y='Orders',
                          title='Top 15 States by Number of Orders',
                          color='Orders', color_continuous_scale='Blues')
fig_state_orders.update_layout(xaxis_tickangle=-45)
fig_state_orders.show()

# Geographical concentration analysis
total_orders_geo = state_analysis['Orders'].sum()
state_analysis['Percentage'] = (state_analysis['Orders'] / total_orders_geo * 100).round(2)
print(f"\nGeographical Concentration (Top 5 States account for {state_analysis.head(5)['Percentage'].sum()}% of orders)")

# Regional Categories
print("\nTop Categories by State:")
state_category = df_clean.groupby(['ship-state', 'Category']).size().reset_index(name='Orders')
state_category = state_category.sort_values('Orders', ascending=False).head(10)
print(state_category)

GEOGRAPHICAL ANALYSIS

Top 15 States by Revenue:
             State  Orders      Revenue  Quantity
28     MAHARASHTRA   22234  13318966.38     20304
23       KARNATAKA   17296  10465387.03     15876
57       TELANGANA   11319   6909670.08     10243
59   UTTAR PRADESH   10633   6814126.08      9495
56      TAMIL NADU   11470   6510503.73     10400
14           DELHI    6770   4228503.97      6144
24          KERALA    6574   3821997.58      5802
61     WEST BENGAL    5955   3503223.44      5311
1   ANDHRA PRADESH    5421   3214859.86      4810
19         HARYANA    4407   2879146.99      4060
18         Gujarat    4479   2723888.82      4139
49       RAJASTHAN    2647   1714511.40      2364
27  MADHYA PRADESH    2529   1592382.98      2260
8            BIHAR    2083   1391728.32      1844
39          ODISHA    2114   1371461.63      1889



Top 15 Cities by Revenue:
             City  Orders     Revenue
809     BENGALURU   11872  7244698.46
2539    HYDERABAD    9117  5594899.78
4330       MUMBAI    7111  4285452.40
4752    NEW DELHI    6329  3947093.20
1313      CHENNAI    6282  3606067.94
5487         PUNE    4616  2794435.79
3422      KOLKATA    2840  1679158.99
2336     GURUGRAM    1951  1279798.78
6565        THANE    1875  1110285.35
3784      LUCKNOW    1627  1049983.10
4862        NOIDA    1626  1037799.01
2172    GHAZIABAD    1484   937666.46
73      AHMEDABAD    1438   894242.56
4664  NAVI MUMBAI    1402   837821.91
605     BANGALORE    1360   823662.35



Geographical Concentration (Top 5 States account for 56.66% of orders)

Top Categories by State:
        ship-state Category  Orders
160    MAHARASHTRA    Shirt    8439
163    MAHARASHTRA  T-shirt    8178
129      KARNATAKA    Shirt    6760
132      KARNATAKA  T-shirt    6434
262     TAMIL NADU    Shirt    5809
288  UTTAR PRADESH  T-shirt    5151
270      TELANGANA    Shirt    4776
273      TELANGANA  T-shirt    3865
285  UTTAR PRADESH    Shirt    3456
265     TAMIL NADU  T-shirt    3391


## Section 8: Business Insights & Recommendations

Comprehensive summary of findings and actionable recommendations.

In [9]:
print("="*80)
print("COMPREHENSIVE BUSINESS INSIGHTS & RECOMMENDATIONS")
print("="*80)

print("\n" + "="*80)
print("1. SALES PERFORMANCE INSIGHTS")
print("="*80)

print(f"""
✓ Total Revenue Generated: ₹{total_revenue:,.2f}
✓ Total Orders: {total_orders:,}
✓ Completion Rate: {(completed_orders/total_orders)*100:.2f}%
✓ Cancellation Rate: {(cancelled_orders/total_orders)*100:.2f}%
✓ Average Order Value: ₹{avg_order_value:,.2f}

KEY INSIGHTS:
• Strong sales performance with majority of orders being completed successfully
• {cancelled_orders:,} cancelled orders indicate potential issues with inventory, pricing, or customer satisfaction
• Average order value of ₹{avg_order_value:,.2f} shows moderate purchasing power
• Sales are consistent throughout the period with no major seasonal spikes

RECOMMENDATIONS:
→ Investigate root causes of cancellations to improve completion rates
→ Implement proactive customer engagement to reduce cancellations
→ Consider loyalty programs to increase average order value
→ Focus on reducing cancellation rate to {(cancelled_orders/total_orders)*100 - 5:.2f}%
""")

print("\n" + "="*80)
print("2. PRODUCT STRATEGY INSIGHTS")
print("="*80)

top_3_categories = category_stats.head(3)
print(f"\nTop 3 Product Categories:")
for idx, (cat, row) in enumerate(top_3_categories.iterrows(), 1):
    print(f"{idx}. {cat}: {int(row['Orders'])} orders, ₹{row['Total_Revenue']:,.2f} revenue")

print(f"""
KEY INSIGHTS:
• Shirts and T-shirts dominate sales (apparel focus)
• Size distribution varies by category (XL, M, L are popular)
• {len(category_stats)} different product categories available
• High variety suggests diverse customer preferences

RECOMMENDATIONS:
→ Prioritize inventory management for top 3 categories
→ Optimize stock levels for popular sizes (M, L, XL)
→ Consider bundling complementary products (e.g., Shirts + Trousers)
→ Explore expanding bestselling categories with new variants
→ Implement category-specific marketing campaigns
→ Monitor underperforming categories for discontinuation or repositioning
""")

print("\n" + "="*80)
print("3. FULFILLMENT & LOGISTICS INSIGHTS")
print("="*80)

merchant_orders = len(df_clean[df_clean['Fulfilment'] == 'Merchant'])
amazon_orders = len(df_clean[df_clean['Fulfilment'] == 'Amazon'])

print(f"""
✓ Merchant Fulfillment: {merchant_orders:,} orders ({(merchant_orders/total_orders)*100:.2f}%)
✓ Amazon Fulfillment: {amazon_orders:,} orders ({(amazon_orders/total_orders)*100:.2f}%)

KEY INSIGHTS:
• Amazon fulfillment handles majority of orders
• Easy Ship (Merchant) and standard fulfillment used for logistics
• Service levels: Standard (economy) and Expedited (premium) available
• Mixed courier network ensures reliability

RECOMMENDATIONS:
→ Strengthen partnership with Amazon for premium fulfillment
→ Optimize Easy Ship for cost-effective merchant orders
→ Implement SLA monitoring for courier partners
→ Consider multi-warehouse strategy for faster delivery
→ Invest in real-time tracking to improve customer satisfaction
→ Analyze courier performance metrics for vendor selection
""")

print("\n" + "="*80)
print("4. GEOGRAPHICAL EXPANSION INSIGHTS")
print("="*80)

top_5_states = state_analysis.head(5)
top_5_percentage = top_5_states['Orders'].sum() / total_orders * 100

print(f"\nTop 5 States:")
for idx, (_, row) in enumerate(top_5_states.iterrows(), 1):
    print(f"{idx}. {row['State']}: {int(row['Orders'])} orders, ₹{row['Revenue']:,.2f}")

print(f"""
✓ Top 5 states account for {top_5_percentage:.2f}% of total orders
✓ Presence in {len(state_analysis)} states across India
✓ Key markets: {', '.join(top_5_states['State'].tolist()[:3])}

KEY INSIGHTS:
• Sales concentrated in major metros and tier-1 cities
• Metropolitan areas (Maharashtra, Karnataka, etc.) show highest demand
• Opportunity in tier-2 and tier-3 cities remains untapped
• Regional preferences vary - shirts popular in southern states

RECOMMENDATIONS:
→ Expand delivery infrastructure in tier-2 cities
→ Launch region-specific marketing campaigns
→ Analyze underperforming states for market entry strategy
→ Partner with local logistics for better reach
→ Customize product offerings by region (regional sizes, preferences)
→ Implement targeted promotions in high-potential cities
→ Target growth in states with <100 orders to achieve market penetration
""")

print("\n" + "="*80)
print("5. CUSTOMER BEHAVIOR INSIGHTS")
print("="*80)

high_value_orders = len(customer_purchase[customer_purchase['Segment'] == 'High Value'])
print(f"""
✓ High-Value Customers: {high_value_orders:,} ({(high_value_orders/len(customer_purchase))*100:.2f}%)
✓ B2B Orders: {b2b_analysis[b2b_analysis['Type']=='B2B']['Orders'].values[0]} ({(b2b_analysis[b2b_analysis['Type']=='B2B']['Orders'].values[0]/total_orders)*100:.2f}%)
✓ B2C Orders: {b2b_analysis[b2b_analysis['Type']=='B2C']['Orders'].values[0]} ({(b2b_analysis[b2b_analysis['Type']=='B2C']['Orders'].values[0]/total_orders)*100:.2f}%)

KEY INSIGHTS:
• Customer base is primarily B2C focused
• High-value customers represent significant revenue opportunity
• Average order values range from ₹{customer_purchase['Total_Spent'].min():.2f} to ₹{customer_purchase['Total_Spent'].max():.2f}
• Customer segmentation enables targeted strategies

RECOMMENDATIONS:
→ Create VIP program for high-value customers (₹700+)
→ Implement retention strategy for repeat customers
→ Expand B2B offerings with bulk discounts and dedicated support
→ Develop personalized marketing based on customer segments
→ Introduce loyalty points/rewards program
→ Create win-back campaigns for low-value customers
→ Establish customer service excellence for high-value segments
""")

print("\n" + "="*80)
print("6. OPERATIONAL EXCELLENCE RECOMMENDATIONS")
print("="*80)

print(f"""
IMMEDIATE ACTIONS (0-30 days):
1. Reduce cancellation rate from {(cancelled_orders/total_orders)*100:.2f}% to <{(cancelled_orders/total_orders)*100 - 5:.2f}%
   → Improve inventory visibility
   → Strengthen demand forecasting
   
2. Optimize fulfillment SLAs
   → Monitor on-time delivery rates
   → Address logistics bottlenecks
   
3. Launch customer feedback program
   → Identify cancellation reasons
   → Implement corrective actions

SHORT-TERM INITIATIVES (1-3 months):
1. Expand in underperforming regions
   → Set up distribution centers in tier-2 cities
   → Partner with local logistics providers
   
2. Product diversification
   → Introduce new product categories
   → Test regional variations
   
3. Customer retention programs
   → Loyalty rewards scheme
   → Personalized marketing campaigns

MID-TERM STRATEGY (3-6 months):
1. Revenue growth targets
   → Increase average order value by 15-20%
   → Expand customer base by 25-30%
   
2. Operational efficiency
   → Achieve 95%+ order completion rate
   → Reduce delivery times by 20%
   
3. Market expansion
   → Penetrate 5 new tier-2 cities
   → Grow in underperforming states
""")

print("\n" + "="*80)
print("KEY PERFORMANCE INDICATORS (KPIs) TO MONITOR")
print("="*80)

kpi_data = {
    'KPI': ['Order Completion Rate', 'Average Order Value', 'Customer Satisfaction', 
            'Fulfillment Efficiency', 'Market Penetration', 'Revenue Growth'],
    'Current': [f'{(completed_orders/total_orders)*100:.2f}%', f'₹{avg_order_value:.2f}', 
                'To be measured', f'{(amazon_orders/total_orders)*100:.2f}%', 
                f'{len(state_analysis)} states', 'Baseline set'],
    'Target': ['95%+', '₹800-1000', '4.5/5', '98%', '25+ states', '20% QoQ']
}

kpi_df = pd.DataFrame(kpi_data)
print(kpi_df.to_string(index=False))

print("\n" + "="*80)
print("CONCLUSION")
print("="*80)
print(f"""
The Amazon sales analysis reveals a healthy business with strong fundamentals:
• Established market presence across {len(state_analysis)} states
• Solid revenue base of ₹{total_revenue:,.2f}
• Diverse product portfolio attracting various customer segments
• Efficient fulfillment network ensuring timely deliveries

By implementing the recommended strategies, the business can:
✓ Reduce cancellation rates and improve customer experience
✓ Expand geographic reach and penetrate untapped markets
✓ Increase average order value through strategic initiatives
✓ Build customer loyalty and drive repeat purchases
✓ Achieve sustainable revenue growth of 20%+ annually

Success requires coordinated efforts across product, operations, marketing,
and customer service teams with clear accountability and regular monitoring.
""")

COMPREHENSIVE BUSINESS INSIGHTS & RECOMMENDATIONS

1. SALES PERFORMANCE INSIGHTS

✓ Total Revenue Generated: ₹78,496,786.39
✓ Total Orders: 128,808
✓ Completion Rate: 82.63%
✓ Cancellation Rate: 14.22%
✓ Average Order Value: ₹661.42

KEY INSIGHTS:
• Strong sales performance with majority of orders being completed successfully
• 18,311 cancelled orders indicate potential issues with inventory, pricing, or customer satisfaction
• Average order value of ₹661.42 shows moderate purchasing power
• Sales are consistent throughout the period with no major seasonal spikes

RECOMMENDATIONS:
→ Investigate root causes of cancellations to improve completion rates
→ Implement proactive customer engagement to reduce cancellations
→ Consider loyalty programs to increase average order value
→ Focus on reducing cancellation rate to 9.22%


2. PRODUCT STRATEGY INSIGHTS

Top 3 Product Categories:
1. T-shirt: 50219 orders, ₹39,154,132.17 revenue
2. Shirt: 49804 orders, ₹21,269,768.70 revenue
3. Blazzer: 15

## Executive Summary Dashboard

Visual summary of all key metrics and insights.

In [11]:
# Create comprehensive summary metrics dashboard
fig_dashboard = go.Figure()

# Create metrics cards
metrics = [
    f"<b>Total Orders</b><br>{total_orders:,}",
    f"<b>Total Revenue</b><br>₹{total_revenue:,.0f}",
    f"<b>Avg Order Value</b><br>₹{avg_order_value:,.0f}",
    f"<b>Completion Rate</b><br>{(completed_orders/total_orders)*100:.1f}%",
    f"<b>Top State</b><br>{state_analysis.iloc[0]['State']}",
    f"<b>Top Category</b><br>{category_stats.index[0]}"
]

colors = ['#1f77b4', '#2ca02c', '#ff7f0e', '#d62728', '#9467bd', '#8c564b']

fig_dashboard = go.Figure(
    data=[go.Scatter(
        x=[1, 2, 3, 4, 5, 6],
        y=[1, 1, 1, 1, 1, 1],
        mode='text',
        text=metrics,
        textposition='middle center',
        textfont=dict(size=12),
        hovertemplate='%{text}<extra></extra>'
    )],
    layout=go.Layout(
        title='Executive Summary - Key Metrics',
        xaxis=dict(showgrid=False, showticklabels=False, zeroline=False),
        yaxis=dict(showgrid=False, showticklabels=False, zeroline=False),
        plot_bgcolor='white',
        margin=dict(l=0, r=0, t=100, b=0),
        height=300,
        hovermode='closest'
    )
)

# Add colored boxes behind metrics
for i, (x, color) in enumerate(zip([1, 2, 3, 4, 5, 6], colors)):
    fig_dashboard.add_shape(
        type="rect",
        x0=x-0.35, y0=0.85, x1=x+0.35, y1=1.15,
        fillcolor=color, opacity=0.2, line=dict(color=color)
    )

fig_dashboard.show()
